In [1]:
from numpy.random import normal
from numpy import median

data = normal(100, 40, 10000)

# P2 Algorithm for dynamic calculation of quantiles and histograms
# without storing observations
# https://www.cs.wustl.edu/~jain/papers/ftp/psqr.pdf
class P2Algorithm:
    def __init__(self, p, verbose=True):
        self.verbose = verbose
        self.count = 0
        # marker heights
        self.q = []
        # marker positions
        self.n = [1, 2, 3, 4, 5]
        # initial desired positions
        self.n_prime = [1, 2, 3, 4, 5]
        # incremental change to desired positions
        self.dn_prime = [0, p/2, p, (p+1)/2, 1]

    def observe(self, value):
        # sort the first five observations and set marker heights and positions
        if len(self.q) < 5:
            self.q += [value]
            self.q.sort()
        else:
            self._do_algo(value)

    def _find_cell(self, value):
        if value < self.q[0]:
            return 0
        return next((i for i in range(4) if self.q[i] <= value < self.q[i+1]), 3)

    def _do_algo(self, value):
        # find cell k such that marker_heights[i] <= value < marker_heights[i+1]
        k = self._find_cell(value)
        # update extremes if necessary
        self.q[0] = min(self.q[0], value)
        self.q[4] = max(self.q[4], value)

        if self.verbose:
            print("Observed value: ", value)
            print("Fits after marker: ", k+1)
    
        # increase of positions marker k+1 through 4 by 1
        for i in range(k+1, 5):
            self.n[i] += 1

        if self.verbose:
            print("Marker position after observation: ", self.n)

        # update desired positions for all markers
        self.n_prime = [n + dn for n, dn in zip(self.n_prime, self.dn_prime)]

        if self.verbose:
            print("Desired marker position: ", self.n_prime)
        
        adjusted = []
        # move markers to desired positions
        for i in range(1, 4):
            d = self.n_prime[i] - self.n[i]
            move_right = (d >= 1 and (self.n[i+1] - self.n[i]) > 1)
            move_left = (d <= -1 and (self.n[i] - self.n[i-1]) > 1)
            if move_right or move_left:
                adjusted += [i]
                d = -1 if d < 0 else 1 # get sign of d
                q_temp = self.q[i] + (d / (self.n[i+1] - self.n[i-1])) \
                    * ((self.n[i] - self.n[i-1] + d) * ((self.q[i+1] - self.q[i]) / (self.n[i+1] - self.n[i])) \
                    + (self.n[i+1] - self.n[i] - d) * ((self.q[i] - self.q[i-1]) / (self.n[i] - self.n[i-1])))
                
                if self.q[i - 1] < q_temp < self.q[i + 1]:
                    self.q[i] = q_temp
                else:
                    self.q[i] = self.q[i] + d * ((self.q[i + d] - self.q[i]) / (self.n[i + d] - self.n[i]))

                self.n[i] += d

        if self.verbose:
            print("Adjust markers", adjusted)
            print("New marker positions", self.n)
            print("Marker heights: ", self.q)
            print()

    @property
    def quantile(self):
        return self.q[2]

p2 = P2Algorithm(0.5)
for value in data:
    p2.observe(value)

print(f"True median: {median(data)}")
print(f"Approximate median: {p2.quantile}")


Observed value:  208.06537674767668
Fits after marker:  4
Marker position after observation:  [1, 2, 3, 4, 6]
Desired marker position:  [1, 2.25, 3.5, 4.75, 6]
Adjust markers []
New marker positions [1, 2, 3, 4, 6]
Marker heights:  [43.70083727117516, 82.0290982561684, 91.50417805138414, 113.11522806783117, 208.06537674767668]

Observed value:  62.28141743002383
Fits after marker:  1
Marker position after observation:  [1, 3, 4, 5, 7]
Desired marker position:  [1, 2.5, 4.0, 5.5, 7]
Adjust markers []
New marker positions [1, 3, 4, 5, 7]
Marker heights:  [43.70083727117516, 82.0290982561684, 91.50417805138414, 113.11522806783117, 208.06537674767668]

Observed value:  173.4182678754613
Fits after marker:  4
Marker position after observation:  [1, 3, 4, 5, 8]
Desired marker position:  [1, 2.75, 4.5, 6.25, 8]
Adjust markers [3]
New marker positions [1, 3, 4, 6, 8]
Marker heights:  [43.70083727117516, 82.0290982561684, 91.50417805138414, 139.74577785602892, 208.06537674767668]

Observed valu

In [2]:
data

array([43.70083727, 91.50417805, 82.02909826, ..., 91.99628594,
       87.29261778, 46.91444277])